In [2]:
import collections
import nbimporter
import basicSim
from tqdm import tqdm
import csv

In [4]:
def read_triples(file_path):
    """
    从指定文件中读取用户-物品-评分的三元组。
    
    参数：
        file_path (str): 指定文件路径，例如 'rating_index.tsv'。
        
    返回：
        list of tuples: 返回一个包含 (user, item, rating) 三元组的列表。
    """
    triples = []  # 初始化一个空列表用于存储三元组
    with open(file_path, 'r', newline='') as file:
        reader = csv.reader(file, delimiter='\t')  # 使用制表符分隔
        for row in reader:
            user, item, rating = map(int, row)  # 转换为整数类型
            triples.append((user, item, rating))  # 将三元组添加到列表中
    return triples

In [6]:
triples = read_triples("rating_index.tsv")
triples

[(195, 1273, 0),
 (185, 1, 0),
 (21, 735, 0),
 (243, 543, 0),
 (165, 717, 0),
 (297, 612, 1),
 (114, 941, 0),
 (252, 599, 1),
 (304, 571, 0),
 (5, 304, 0),
 (61, 5, 0),
 (285, 208, 1),
 (199, 644, 1),
 (209, 1174, 0),
 (223, 675, 0),
 (302, 980, 0),
 (121, 1468, 1),
 (193, 832, 0),
 (290, 1581, 1),
 (233, 808, 0),
 (118, 911, 1),
 (166, 652, 1),
 (298, 1213, 1),
 (290, 1158, 0),
 (307, 760, 1),
 (94, 1159, 0),
 (37, 877, 1),
 (101, 1507, 0),
 (62, 1392, 1),
 (159, 1517, 1),
 (49, 1029, 0),
 (300, 1483, 1),
 (224, 202, 1),
 (289, 117, 1),
 (96, 1300, 0),
 (156, 832, 1),
 (180, 276, 0),
 (277, 1137, 1),
 (275, 174, 0),
 (6, 865, 1),
 (9, 639, 1),
 (283, 1250, 1),
 (200, 1374, 0),
 (275, 251, 0),
 (286, 78, 1),
 (245, 1074, 1),
 (241, 679, 1),
 (248, 131, 1),
 (98, 150, 1),
 (177, 1341, 0),
 (250, 868, 1),
 (80, 732, 0),
 (259, 1310, 1),
 (24, 985, 1),
 (58, 1238, 1),
 (71, 838, 0),
 (86, 1489, 1),
 (289, 226, 1),
 (41, 1490, 1),
 (291, 967, 1),
 (114, 1316, 0),
 (19, 910, 0),
 (200, 234,

In [8]:
def getSet(triples):
    """
    根据用户-物品-评分三元组构建一个用户-物品集合字典。
    
    参数：
        triples (list of tuples): 每个元组包含 (user, item, rating)，表示用户对某个物品的喜欢与否。
        
    返回：
        dict: 一个字典，其中键是用户 ID，值是该用户喜欢的物品集合。
    
    说明：
        1. 遍历输入的三元组列表 triples，每个三元组包含用户 ID、物品 ID 和喜欢与否。
        2. 对于评分等于 1 的物品，将该物品 ID 添加到对应用户的物品集合中。
        3. 使用 collections.defaultdict 来初始化每个用户的物品集合，便于自动处理空集合。
    """
    user_items = collections.defaultdict(set)
    for u, i, r in triples:
        if r == 1:
            user_items[u].add(i)
    return user_items

In [10]:
user_items = getSet(triples)
user_items

defaultdict(set,
            {297: {5,
              6,
              15,
              16,
              18,
              22,
              57,
              68,
              79,
              89,
              110,
              117,
              175,
              202,
              226,
              228,
              243,
              274,
              285,
              307,
              310,
              333,
              349,
              356,
              372,
              382,
              387,
              388,
              441,
              450,
              471,
              497,
              499,
              529,
              585,
              599,
              612,
              621,
              633,
              672,
              674,
              696,
              700,
              718,
              732,
              760,
              780,
              829,
              839,
              843,
              854,
              886,
  

In [12]:
def knn4set_userCF(trainset,k,sim_method):
    """
    计算每个商品在给定训练集中基于相似度的 K 相似商品。

    参数：
        trainset (dict): 一个字典，键是用户 ID，值是该用户的物品集合。
        k (int): 每个用户的近邻数量。
        sim_method (function): 一个相似度计算方法，用于计算两个用户之间的相似度。该方法接受两个集合作为输入，返回一个相似度值。

    返回：
        dict: 一个字典，其中键是用户 ID，值是与该用户最相似的 K 个用户的 ID 列表。

    说明：
        1. 对于训练集中的每个用户 u1，遍历所有其他用户 u2 以计算相似度。
        2. 只对拥有共同物品的用户对（u1 和 u2）进行相似度计算。
        3. 忽略 u1 自身以及没有共同物品的用户。
        4. 计算相似度后，将每个 u1 的所有其他用户按相似度排序并选取前 K 个用户作为其近邻。
    """
    sims = {}
    for u1 in tqdm(trainset):
        ulist = []
        for u2 in trainset:
            if u1 == u2 or len(trainset[u1] & trainset[u2]) == 0:
                continue
            sim = sim_method(trainset[u1],trainset[u2])
            ulist.append((sim,u2))
        sims[u1] = [i[1] for i in sorted(ulist,reverse=True)[:k]]
    return sims

In [16]:
user_sims = knn4set_userCF(user_items,k=3,sim_method=basicSim.Jaccard)
user_sims

100%|███████████████████████████████████████████████████████████████████████████████| 942/942 [00:04<00:00, 193.69it/s]


{297: [312, 397, 693],
 252: [849, 487, 898],
 285: [513, 302, 275],
 199: [471, 881, 108],
 121: [614, 84, 242],
 290: [302, 275, 863],
 118: [331, 177, 863],
 166: [320, 425, 715],
 298: [17, 536, 408],
 307: [58, 302, 6],
 37: [619, 900, 329],
 62: [1, 225, 589],
 159: [591, 213, 114],
 300: [863, 177, 803],
 224: [390, 349, 369],
 289: [253, 41, 483],
 156: [466, 525, 677],
 277: [38, 672, 667],
 6: [473, 58, 405],
 9: [5, 388, 746],
 283: [610, 46, 148],
 286: [53, 56, 714],
 245: [267, 714, 302],
 241: [894, 749, 705],
 248: [591, 342, 275],
 98: [346, 452, 331],
 250: [116, 167, 431],
 259: [811, 728, 840],
 24: [649, 747, 912],
 58: [473, 456, 845],
 86: [483, 647, 891],
 41: [881, 483, 532],
 291: [621, 888, 428],
 200: [326, 302, 215],
 137: [5, 81, 932],
 59: [473, 931, 311],
 56: [402, 431, 167],
 222: [763, 653, 286],
 188: [380, 5, 839],
 193: [5, 297, 378],
 177: [415, 863, 221],
 126: [701, 583, 551],
 221: [550, 456, 177],
 266: [822, 885, 248],
 10: [270, 296, 720],
 

In [17]:
def get_recommodations_by_userCF(user_sims,user_o_set):
    """
    基于用户协同过滤（userCF）推荐物品。
    
    参数：
        user_sims (dict): 用户相似度字典，其中键是用户 u，值是与该用户相似的用户列表。
        user_o_set (dict): 每个用户已拥有物品的集合，键是用户 u，值是该用户已拥有的物品集合。
        
    返回：
        dict: 用户推荐字典，其中键是用户 u，值是推荐给该用户的物品集合。
    
    功能：
        该函数遍历每个用户 u 的相似用户列表，并从相似用户中找到用户 u 尚未拥有的物品，
        将这些物品推荐给用户 u。
    """
    recommodations = collections.defaultdict(set)
    for u in user_sims:
        for sim_u in user_sims[u]:
            recommodations[u] |= (user_o_set[sim_u]-user_o_set[u])
    return recommodations

In [28]:
recommodations = get_recommodations_by_userCF(user_sims,user_items)
recommodations

defaultdict(set,
            {297: {2,
              17,
              33,
              94,
              105,
              111,
              114,
              116,
              119,
              137,
              138,
              145,
              159,
              169,
              178,
              179,
              185,
              201,
              216,
              233,
              246,
              271,
              272,
              273,
              278,
              281,
              294,
              312,
              313,
              315,
              323,
              327,
              344,
              345,
              359,
              360,
              379,
              391,
              408,
              442,
              456,
              462,
              463,
              475,
              480,
              484,
              501,
              505,
              508,
              510,
              541,
              